In [1]:
import torch
import torch.nn as nn
from torch import Tensor
import torch.nn.functional as F
import math

In [42]:
class Attn(nn.Module):
    def __init__(self, emb_dim, q_dim, k_dim):
        super().__init__()
        self.Wq = nn.Linear(emb_dim, q_dim)
        self.Wk = nn.Linear(emb_dim, k_dim)
        self.Wv = nn.Linear(emb_dim, k_dim)
        
    def forward(self, x, z):
        Q = self.Wq(x)
        K = self.Wk(z)
        V = self.Wv(z)
#         print(K.shape)
        S = Q.bmm(K.transpose(1,2))
        # uhh masking here
#         print(S.shape)
        sm = F.softmax(torch.div(S,torch.sqrt(torch.tensor(x.shape[-1]))),dim=-1)
#         print(sm.shape)
#         print(V.shape)
        return sm.bmm(V)
    
class MHAttn(nn.Module):
    def __init__(self, num_heads, emb_dim, q_dim, k_dim):
        super().__init__()
        self.heads = nn.ModuleList([Attn(emb_dim, q_dim, k_dim) for _ in range(num_heads)])
        self.Wo = nn.Linear(num_heads * k_dim, emb_dim)
        
    def forward(self, x, z):
        subAttns = torch.cat([h(x,z) for h in self.heads], dim=-1)
        return self.Wo(subAttns)
        
# encoder is definitionally self-attn
class EncoderBlock(nn.Module):
    def __init__(self, emb_dim, z_dim, heads):
        super().__init__()
        self.attn = MHAttn(heads, emb_dim, z_dim, z_dim)
        self.ln1 = nn.LayerNorm(emb_dim)
        self.ln2 = nn.LayerNorm(emb_dim)
        self.ff1 = nn.Linear(emb_dim,emb_dim)
        self.ff2 = nn.Linear(emb_dim,emb_dim)
        
    def forward(self, z):
        z = z + self.attn(z,z)
        z = self.ln1(z)
        z = z + self.ff2(F.relu(self.ff1(z)))
        return self.ln2(z)
    
class DecoderBlock(nn.Module):
    def __init__(self, emb_dim, x_dim, z_dim, heads):
        super().__init__()
        self.attn = MHAttn(heads, emb_dim, x_dim, z_dim)
        self.ln1 = nn.LayerNorm(emb_dim)
        self.ln2 = nn.LayerNorm(emb_dim)
        self.ln3 = nn.LayerNorm(emb_dim)
        self.ff1 = nn.Linear(emb_dim,emb_dim)
        self.ff2 = nn.Linear(emb_dim,emb_dim)
        
    def forward(self, x, z):
        x = x + self.attn(x,x)
        x = self.ln1(x)
        x = x + self.attn(x,z)
        x = self.ln2(x)
        x = x + self.ff2(F.relu(self.ff1(x)))
        return self.ln3(x)
        
# review this

class EDTransformer(nn.Module):
    def __init__(self, embs, pos, emb_dim, x_dim, z_dim, heads, enc_blocks, dec_blocks, out_dim):
        # needs embedding matrix
        # garbage for now
        # positional embedding scheme
        # softmax FF at the end
        super().__init__()
        self.addpos = pos
        self.enc_blocks = enc_blocks
        self.dec_blocks = dec_blocks
        self.encoderBlocks = nn.ModuleList(
            [EncoderBlock(emb_dim, x_dim, heads) for _ in range(enc_blocks)]
        )
        self.decoderBlocks = nn.ModuleList(
            [DecoderBlock(emb_dim, x_dim, z_dim, heads) for _ in range(dec_blocks)]
        )
        self.ff = nn.Linear(emb_dim, 28)
        self.ff2 = nn.Linear(784, out_dim)

    def forward(self, x,z):
        # embed + pos
        x = self.addpos(x.permute(1,0,2)).permute(1,0,2)
        z = self.addpos(z.permute(1,0,2)).permute(1,0,2)
        # loop through encoder blocks
        for i in range(self.enc_blocks):
            z = self.encoderBlocks[i](z)
        # loop through decoder blocks
        for i in range(self.dec_blocks):
            x = self.decoderBlocks[i](x, z)
        # FF and softmax
        x = F.relu(self.ff(x))
        x = torch.flatten(x, start_dim=1)
        return F.softmax(self.ff2(x), dim=-1)
    
class posEncoding(nn.Module):
    def __init__(self, model_dim, dropout, maxlen):
        super().__init__()
        self.dropout = dropout
        position = torch.arange(maxlen).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, model_dim, 2) * (-math.log(10000.0)/model_dim))
#         print("position.shape")
#         print(position.shape)
#         print("div_term.shape")
#         print(div_term.shape)
#         print("model_dim")
#         print(model_dim)
        pe = torch.zeros(maxlen, 1, model_dim)
        pe[:, 0, 0::2] = torch.sin(position * div_term)
        pe[:, 0, 1::2] = torch.cos(position * div_term)
        self.register_buffer("pe", pe)
#         print(self.pe.shape)
    
    def forward(self, x):
#         print("x.shape")
#         print(x.shape)
#         print("self.pe[:x.shape[0]].shape")
#         print(self.pe[:x.shape[0]].shape)
        x = x + self.pe[:x.shape[0]]
        return x #self.dropout(x)
        
        


In [3]:
exAttn = Attn(256, 32, 32)

In [4]:
# sequence of 8 words
x = torch.randn(1,8,256)
# seq of 10
z = torch.randn(1,10,256)

In [5]:
# three seqs of 8 words
x = torch.randn(3,8,256)
# three seqs of 10
z = torch.randn(3,10,256)

In [6]:
res = exAttn(x,x)
res.shape

torch.Size([3, 8, 32])


torch.Size([3, 8, 32])

In [7]:
exMHA = MHAttn(8, 256, 32, 32)

In [8]:
mhres = exMHA(x,x)
mhres.shape

torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])


torch.Size([3, 8, 256])

In [9]:
exEB = EncoderBlock(256, 32, 8)

In [10]:
ebres = exEB(x)

torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])


In [11]:
ebres.shape

torch.Size([3, 8, 256])

In [12]:
exDB = DecoderBlock(256, 32, 32, 8)

In [13]:
dbres = exDB(x, z)

torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])


In [14]:
dbres.shape

torch.Size([3, 8, 256])

In [15]:
exPE = posEncoding(28, 0, 10000)

position.shape
torch.Size([10000, 1])
div_term.shape
torch.Size([14])
model_dim
28
torch.Size([10000, 1, 28])


In [36]:
exEDT = EDTransformer(None, exPE, 256, 32, 32, 8, 3,3,10)

In [37]:
edtres = exEDT(x,z)

x.shape
torch.Size([8, 3, 256])
self.pe[:x.shape[0]].shape
torch.Size([8, 1, 256])
x.shape
torch.Size([10, 3, 256])
self.pe[:x.shape[0]].shape
torch.Size([10, 1, 256])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 8, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])
torch.Size([3, 10, 32])


In [38]:
edtres.shape

torch.Size([3, 8, 10])

In [39]:
from torchsummary import summary
summary(exEDT, [(8,256),(10,256)])


x.shape
torch.Size([8, 2, 256])
self.pe[:x.shape[0]].shape
torch.Size([8, 1, 256])
x.shape
torch.Size([10, 2, 256])
self.pe[:x.shape[0]].shape
torch.Size([10, 1, 256])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 8, 32])
torch.Size([2, 8, 32])
torch.Size([2, 8, 32])
torch.Size([2, 8, 32])
torch.Size([2, 8, 32])
torch.Size([2, 8, 32])
torch.Size([2, 8, 32])
torch.Size([2, 8, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])
torch.Size([2, 10, 32])


In [16]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader
import torchvision

In [17]:
mnist = torchvision.datasets.MNIST("./mnist", download=True)
mnistVal = torchvision.datasets.MNIST("./mnist", train=False, download=True)


In [18]:
from PIL import Image
import torchvision.transforms as transforms
import math

In [19]:
type(mnist)

torchvision.datasets.mnist.MNIST

In [20]:
transform = transforms.Compose([
    transforms.PILToTensor(),
])

traindata, trainlabels = zip(*[(transform(x[0])/255.0, x[1]) for x in mnist])
valdata, vallabels = zip(*[(transform(x[0])/255.0, x[1]) for x in mnistVal])


/Users/ethangoldfarb/miniconda3/lib/python3.8/site-packages/torchvision/transforms/functional.py:169: UserWarning: The given NumPy array is not writeable, and PyTorch does not support non-writeable tensors. This means you can write to the underlying (supposedly non-writeable) NumPy array using the tensor. You may want to copy the array to protect its data or make it writeable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at  ../torch/csrc/utils/tensor_numpy.cpp:143.)
  img = torch.as_tensor(np.asarray(pic))


In [21]:
print(len(trainlabels))
len(traindata)

60000


60000

In [22]:
# print(trainlabels[0])
# print(traindata[0])
valdata = torch.cat(valdata)
vallabels = torch.cat([torch.tensor([y]) for y in vallabels])

In [23]:
print(trainlabels[0])
print(traindata[0])
traindata = torch.cat(traindata)
trainlabels = torch.cat([torch.tensor([y]) for y in trainlabels])

5
tensor([[[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000],
         [0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000],
         [0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000],
         [0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.000

In [24]:
traindata.shape

torch.Size([60000, 28, 28])

In [25]:
train_ds = TensorDataset(traindata, trainlabels)
val_ds = TensorDataset(valdata, vallabels)

In [47]:
train_dl = DataLoader(train_ds, batch_size=32, shuffle=False)
val_dl = DataLoader(val_ds, batch_size=32, shuffle=False)

In [43]:
exPE2 = posEncoding(28, 0, 10000)
lmaoOhLawd = EDTransformer(None, exPE2, 28, 4, 4, 7, 3,3,10)

position.shape
torch.Size([10000, 1])
div_term.shape
torch.Size([14])
model_dim
28
torch.Size([10000, 1, 28])


In [44]:
# s, b, e order
exPE2(torch.ones(28,1,28)).shape

x.shape
torch.Size([28, 1, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])


torch.Size([28, 1, 28])

In [45]:
from torchsummary import summary
summary(lmaoOhLawd, [(28,28),(28,28)])


x.shape
torch.Size([28, 2, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 2, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.Size([2, 28, 4])
torch.

In [ ]:
# todo: train with text data (quick)
# next: LC babyyy

In [ ]:
n_epochs = 5
opt = optim.AdamW(lmaoOhLawd.parameters())
loss_func = F.cross_entropy

for i in range(n_epochs):
    for xtb, ytb in train_dl:
#         print(xtb.shape)
        preds = lmaoOhLawd(xtb, xtb)
#         print(preds.shape)
        loss = loss_func(preds, ytb)
        loss.backward()
        opt.step()
        opt.zero_grad()
        with torch.no_grad():
            currvalloss = sum([loss_func(lmaoOhLawd(xtb, xtb), ytb) for xtb, ytb in val_dl])
            print("val loss epoch ", i, ":", currvalloss)

torch.Size([32, 28, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32,

torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
x.shape
torch.Si

x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 

torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 

torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 

...

torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 

torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 

x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 

torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([32, 

torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
x.shape
torch.Size([28, 32, 28])
self.pe[:x.shape[0]].shape
torch.Size([28, 1, 28])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 28, 4])
torch.Size([32, 

In [225]:
# three seqs of 8 words
# x = torch.randn(3,8,256)
# three seqs of 10
# z = torch.randn(3,10,256)
peres = exPE(x)

In [289]:
lol = torch.ones(28,28)

In [292]:
lol.resize((28**2)).shape

torch.Size([784])